In [92]:
import xgboost as xgb
import numpy as np
import pandas as pd
import pandas_profiling
from sklearn.linear_model import LogisticRegression
from sklearn.model_selection import cross_val_score, RandomizedSearchCV, StratifiedKFold, StratifiedShuffleSplit, GridSearchCV
from sklearn.model_selection import train_test_split
from sklearn.ensemble import RandomForestClassifier
from sklearn.metrics import roc_auc_score
pd.options.display.max_columns = None
from sklearn.ensemble import BaggingClassifier
from scipy.sparse import hstack
from validation import Preprocessing, cross_val

In [2]:
train = pd.read_csv('../data/train_cleaned.csv', sep="\t")
test = pd.read_csv('../data/test_cleaned.csv', sep="\t")
train.drop('Unnamed: 0', axis = 1, inplace=True)

In [3]:
X, y = train.drop("0", axis = 1), train["0"]
combined = pd.concat([ train.drop("0", axis = 1), test ])

In [84]:
X_train, X_test, y_train, y_test = train_test_split(train, train['0'], test_size=0.1)

In [76]:
skf = StratifiedKFold(n_splits = 5, shuffle = True)

In [6]:
logmodel = LogisticRegression(C=0.06, class_weight='balanced')

In [7]:
%%time
results = cross_val_score(logmodel, X, y, cv=skf, scoring='roc_auc').mean()
#scores.append({results, logmodel, skf})
results

CPU times: user 12.7 s, sys: 667 ms, total: 13.4 s
Wall time: 13.7 s


In [8]:
results

0.7282092706702565

In [56]:
def get_auc_lr_valid(X, y, C=0.06, ratio = 0.7, seed=17):
    train_len = int(ratio * X.shape[0])
    X_train = X.iloc[:train_len, :]
    X_valid = X.iloc[train_len:, :]
    y_train = y.iloc[:train_len]
    y_valid = y.iloc[train_len:]
    
    logit = LogisticRegression(C=C, n_jobs=-1, random_state=seed, class_weight='balanced')
    
    logit.fit(X_train, y_train)
    
    valid_pred = logit.predict_proba(X_valid)[:, 1]
    
    return roc_auc_score(y_valid, valid_pred)

In [57]:
get_auc_lr_valid(X, y)

/anaconda3/lib/python3.6/site-packages/sklearn/linear_model/logistic.py:1228: UserWarning: 'n_jobs' > 1 does not have any effect when 'solver' is set to 'liblinear'. Got 'n_jobs' = -1.
  " = {}.".format(self.n_jobs))


0.7330512974570491

In [11]:
def get_auc_lr_by_split(X, y, C=0.06, seed=17):
    X_train, X_valid, y_train, y_valid = train_test_split(X, y, test_size=0.2)
    
    logit = LogisticRegression(C=C, n_jobs=-1, random_state=seed)
    
    logit.fit(X_train, y_train)
    
    valid_pred = logit.predict_proba(X_valid)[:, 1]
    
    return roc_auc_score(y_valid, valid_pred)

In [12]:
get_auc_lr_by_split(X, y)

/anaconda3/lib/python3.6/site-packages/sklearn/linear_model/logistic.py:1228: UserWarning: 'n_jobs' > 1 does not have any effect when 'solver' is set to 'liblinear'. Got 'n_jobs' = -1.
  " = {}.".format(self.n_jobs))


0.7262478409623447

In [13]:
parameters = {"C": [0.04, 0.05, 0.06, 0.07, 0.08, 0.09], "solver": ["sag"]}
lg = LogisticRegression()

In [14]:
def calc(model, X, y):
    r_grid_search = RandomizedSearchCV(model, parameters, scoring ='roc_auc', n_iter=6, cv=skf, random_state=42)
    r_grid_search = r_grid_search.fit(X, y)
    print(r_grid_search.best_params_, r_grid_search.best_score_)
    return r_grid_search

In [15]:
calc(lg, X, y)

{'solver': 'sag', 'C': 0.09} 0.7280050830888116


RandomizedSearchCV(cv=StratifiedKFold(n_splits=10, random_state=42, shuffle=True),
          error_score='raise',
          estimator=LogisticRegression(C=1.0, class_weight=None, dual=False, fit_intercept=True,
          intercept_scaling=1, max_iter=100, multi_class='ovr', n_jobs=1,
          penalty='l2', random_state=None, solver='liblinear', tol=0.0001,
          verbose=0, warm_start=False),
          fit_params=None, iid=True, n_iter=6, n_jobs=1,
          param_distributions={'C': [0.04, 0.05, 0.06, 0.07, 0.08, 0.09], 'solver': ['sag']},
          pre_dispatch='2*n_jobs', random_state=42, refit=True,
          return_train_score='warn', scoring='roc_auc', verbose=0)

In [40]:
def create_answers(X, y, C=0.06, ratio = 0.7, seed=17):
    train_len = int(ratio * X.shape[0])
    X_train = X.iloc[:train_len, :]
    X_valid = X.iloc[train_len:, :]
    y_train = y.iloc[:train_len]
    y_valid = y.iloc[train_len:]
    
    logit = LogisticRegression(C=C, n_jobs=-1, random_state=seed)
    
    logit.fit(X_train, y_train)
    #predictions = logit.predict(test.drop("0", axis = 1))
    
    valid_pred = logit.predict_proba(test.drop("0", axis = 1))[:, 1]
    
    #print(roc_auc_score(y_valid, valid_pred))
    
    return valid_pred
    

In [41]:
kek = create_answers(X, y) # boosters score 0.73756357

/anaconda3/lib/python3.6/site-packages/sklearn/linear_model/logistic.py:1228: UserWarning: 'n_jobs' > 1 does not have any effect when 'solver' is set to 'liblinear'. Got 'n_jobs' = -1.
  " = {}.".format(self.n_jobs))


In [46]:
submission = pd.DataFrame({'_ID_': test.index})
val = pd.DataFrame(kek, columns=['_VAL_'])
submission= pd.concat([submission, val],axis=1)
submission.to_csv('submissionforboosters.csv', sep=',', encoding='utf-8',index=False)

In [79]:
lg = LogisticRegression(class_weight = 'balanced', n_jobs = -1)
parameters = {'max_features': [0.9, 1.], 'max_samples': [0.4, 0.5, 0.8], "base_estimator__C": [0.05, 0.06]}
bg = BaggingClassifier(lg, random_state = 42, n_estimators = 40, warm_start = True)
gsBC = GridSearchCV(estimator = bg, 
                    param_grid = parameters, 
                    scoring = 'roc_auc', 
                    cv = skf, verbose =2, n_jobs = -1)
gsBC = gsBC.fit(X, y)
print(gsBC.best_score_)

Fitting 5 folds for each of 12 candidates, totalling 60 fits
[CV] base_estimator__C=0.05, max_features=0.9, max_samples=0.4 .......
[CV] base_estimator__C=0.05, max_features=0.9, max_samples=0.4 .......
[CV] base_estimator__C=0.05, max_features=0.9, max_samples=0.4 .......


/anaconda3/lib/python3.6/site-packages/sklearn/linear_model/logistic.py:1228: UserWarning: 'n_jobs' > 1 does not have any effect when 'solver' is set to 'liblinear'. Got 'n_jobs' = -1.
  " = {}.".format(self.n_jobs))


[CV] base_estimator__C=0.05, max_features=0.9, max_samples=0.4 .......


/anaconda3/lib/python3.6/site-packages/sklearn/linear_model/logistic.py:1228: UserWarning: 'n_jobs' > 1 does not have any effect when 'solver' is set to 'liblinear'. Got 'n_jobs' = -1.
  " = {}.".format(self.n_jobs))
/anaconda3/lib/python3.6/site-packages/sklearn/linear_model/logistic.py:1228: UserWarning: 'n_jobs' > 1 does not have any effect when 'solver' is set to 'liblinear'. Got 'n_jobs' = -1.
  " = {}.".format(self.n_jobs))
/anaconda3/lib/python3.6/site-packages/sklearn/linear_model/logistic.py:1228: UserWarning: 'n_jobs' > 1 does not have any effect when 'solver' is set to 'liblinear'. Got 'n_jobs' = -1.
  " = {}.".format(self.n_jobs))
/anaconda3/lib/python3.6/site-packages/sklearn/linear_model/logistic.py:1228: UserWarning: 'n_jobs' > 1 does not have any effect when 'solver' is set to 'liblinear'. Got 'n_jobs' = -1.
  " = {}.".format(self.n_jobs))
/anaconda3/lib/python3.6/site-packages/sklearn/linear_model/logistic.py:1228: UserWarning: 'n_jobs' > 1 does not have any effect whe

/anaconda3/lib/python3.6/site-packages/sklearn/linear_model/logistic.py:1228: UserWarning: 'n_jobs' > 1 does not have any effect when 'solver' is set to 'liblinear'. Got 'n_jobs' = -1.
  " = {}.".format(self.n_jobs))
/anaconda3/lib/python3.6/site-packages/sklearn/linear_model/logistic.py:1228: UserWarning: 'n_jobs' > 1 does not have any effect when 'solver' is set to 'liblinear'. Got 'n_jobs' = -1.
  " = {}.".format(self.n_jobs))
/anaconda3/lib/python3.6/site-packages/sklearn/linear_model/logistic.py:1228: UserWarning: 'n_jobs' > 1 does not have any effect when 'solver' is set to 'liblinear'. Got 'n_jobs' = -1.
  " = {}.".format(self.n_jobs))
/anaconda3/lib/python3.6/site-packages/sklearn/linear_model/logistic.py:1228: UserWarning: 'n_jobs' > 1 does not have any effect when 'solver' is set to 'liblinear'. Got 'n_jobs' = -1.
  " = {}.".format(self.n_jobs))
/anaconda3/lib/python3.6/site-packages/sklearn/linear_model/logistic.py:1228: UserWarning: 'n_jobs' > 1 does not have any effect whe

/anaconda3/lib/python3.6/site-packages/sklearn/linear_model/logistic.py:1228: UserWarning: 'n_jobs' > 1 does not have any effect when 'solver' is set to 'liblinear'. Got 'n_jobs' = -1.
  " = {}.".format(self.n_jobs))
/anaconda3/lib/python3.6/site-packages/sklearn/linear_model/logistic.py:1228: UserWarning: 'n_jobs' > 1 does not have any effect when 'solver' is set to 'liblinear'. Got 'n_jobs' = -1.
  " = {}.".format(self.n_jobs))
/anaconda3/lib/python3.6/site-packages/sklearn/linear_model/logistic.py:1228: UserWarning: 'n_jobs' > 1 does not have any effect when 'solver' is set to 'liblinear'. Got 'n_jobs' = -1.
  " = {}.".format(self.n_jobs))
/anaconda3/lib/python3.6/site-packages/sklearn/linear_model/logistic.py:1228: UserWarning: 'n_jobs' > 1 does not have any effect when 'solver' is set to 'liblinear'. Got 'n_jobs' = -1.
  " = {}.".format(self.n_jobs))
/anaconda3/lib/python3.6/site-packages/sklearn/linear_model/logistic.py:1228: UserWarning: 'n_jobs' > 1 does not have any effect whe

/anaconda3/lib/python3.6/site-packages/sklearn/linear_model/logistic.py:1228: UserWarning: 'n_jobs' > 1 does not have any effect when 'solver' is set to 'liblinear'. Got 'n_jobs' = -1.
  " = {}.".format(self.n_jobs))
/anaconda3/lib/python3.6/site-packages/sklearn/linear_model/logistic.py:1228: UserWarning: 'n_jobs' > 1 does not have any effect when 'solver' is set to 'liblinear'. Got 'n_jobs' = -1.
  " = {}.".format(self.n_jobs))


KeyboardInterrupt: 

In [74]:
%%time
kek = log_reg_GBC(X, y)

KeyboardInterrupt: 

In [20]:
pandas_profiling.ProfileReport(train)

In [21]:
pandas_profiling.ProfileReport(test)

In [22]:
from sklearn.ensemble import AdaBoostClassifier, GradientBoostingClassifier, GradientBoostingRegressor

In [31]:
clf = AdaBoostClassifier(n_estimators=100,random_state=42)
scores = cross_val_score(clf, X, y, scoring='roc_auc')
scores.mean() 

0.7164764717628747

In [26]:
clf

AdaBoostClassifier(algorithm='SAMME.R', base_estimator=None,
          learning_rate=1.0, n_estimators=100, random_state=None)

In [35]:
def gr_b_c():
    gbc = GradientBoostingClassifier()
    scores = cross_val_score(clf, X, y, scoring='roc_auc')
    print(scores.mean())

In [37]:
gr_b_c()

0.7164764717628747


In [241]:
def get_auc_clf_by_split(X, y, seed=17):
    X_train, X_valid, y_train, y_valid = train_test_split(X, y, test_size=0.2)
    
    clf = AdaBoostClassifier(n_estimators=100, random_state=seed)
    
    clf.fit(X_train, y_train)
    
    valid_pred = clf.predict_proba(X_valid)[:, 1]
    
    return roc_auc_score(y_valid, valid_pred)

In [242]:
get_auc_clf_by_split(X, y)

0.7146133636363636

In [86]:
X_train, X_hold, y_train , y_hold = train_test_split(X, y, shuffle=True, test_size=.10) 

In [87]:
skfs = StratifiedKFold(n_splits=5, shuffle=True, random_state=42)
rfc = RandomForestClassifier(random_state=42,max_depth=15, n_jobs=-1, n_estimators=200,oob_score=True, max_features='sqrt')
cross_val(rfc, roc_auc_score, X_train, y_train)

Cross-validation on 5 folds.
0.7160729760402617
0.7108478730655992
0.721447419469463
0.7356252447461167
0.7206044050675137
-----
Mean: 0.7209195836777909


([0.7160729760402617,
  0.7108478730655992,
  0.721447419469463,
  0.7356252447461167,
  0.7206044050675137],
 0.7209195836777909)

In [88]:
cross_val(rfc, roc_auc_score, X_train, y_train)

Cross-validation on 5 folds.
0.7235486102046441
0.7163109236537151
0.7322930716906699
0.7180726424603693
0.7230031436278989
-----
Mean: 0.7226456783274594


([0.7235486102046441,
  0.7163109236537151,
  0.7322930716906699,
  0.7180726424603693,
  0.7230031436278989],
 0.7226456783274594)

In [90]:
from scipy.stats import rankdata
rfc.fit(X_train, y_train)
roc_auc_score(y_hold, rankdata(rfc.predict_proba(X_hold)[:, 1]))

0.7404478812368576

XGBoost!!!!!


In [93]:
boost = xgb.XGBClassifier(n_jobs=-1, learning_rate=0.05)

In [ ]:
cross_val(boost, roc_auc_score, X_train, y_train)

Cross-validation on 5 folds.
0.7085136069776211
0.7224895167080017
0.730329324029355
0.7249334653149431
